In [41]:
import pandas as pd 
import numpy as np
from rdkit import Chem
from rdkit.Chem import AllChem
import numpy as np
from molvs import Standardizer
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, r2_score
import joblib

In [5]:
df = pd.read_csv('KiDatabase.csv')
df.head()


Number    Name Unigene  Ligand ID          Ligand Name  \
0       1  5-HT2C   HTR2C        172  5-Methoxytryptamine   
1       2  5-HT2C   HTR2C        172  5-Methoxytryptamine   
2       3  5-HT2C   HTR2C        172  5-Methoxytryptamine   
3       4  5-HT2C   HTR2C        172  5-Methoxytryptamine   
4       5  5-HT2C   HTR2C        172  5-Methoxytryptamine   

                     SMILES       CAS      NSC       Hotligand species  \
0  COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
1  COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
2  COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
3  COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
4  COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   

           source ki Note  ki Val                Reference Link  
0  Choroid Plexus     NaN    23.4     HOYER, 1989 (J.R.R.)  NaN  
1  Choroid Plexus     NaN    23.4              HOYER, 1988  NaN  
2  Choroid Plexus     NaN    25.1  HOYER, 1988 or 9 (book)  NaN  
3  Choroid Plexus     NaN    43.7    MARKSTEIN ET AL, 1986  NaN  
4  Choroid Plexus     NaN    43.8        ENGEL ET AL, 1986  NaN

In [ ]:
df.index = df['Number']
df.drop(columns=['Number'], inplace=True)

In [11]:
df.head()
#df.columns

Name Unigene  Ligand ID          Ligand Name  \
Number                                                   
1       5-HT2C   HTR2C        172  5-Methoxytryptamine   
2       5-HT2C   HTR2C        172  5-Methoxytryptamine   
3       5-HT2C   HTR2C        172  5-Methoxytryptamine   
4       5-HT2C   HTR2C        172  5-Methoxytryptamine   
5       5-HT2C   HTR2C        172  5-Methoxytryptamine   

                          SMILES       CAS      NSC       Hotligand species  \
Number                                                                        
1       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
2       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
3       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
4       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
5       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   

                source ki Note  ki Val                Reference Link  
Number                                                                
1       Choroid Plexus     NaN    23.4     HOYER, 1989 (J.R.R.)  NaN  
2       Choroid Plexus     NaN    23.4              HOYER, 1988  NaN  
3       Choroid Plexus     NaN    25.1  HOYER, 1988 or 9 (book)  NaN  
4       Choroid Plexus     NaN    43.7    MARKSTEIN ET AL, 1986  NaN  
5       Choroid Plexus     NaN    43.8        ENGEL ET AL, 1986  NaN

In [14]:
print(df.columns)
print(df.shape)

Index(['Name', 'Unigene', 'Ligand ID', ' Ligand Name', 'SMILES', 'CAS', 'NSC',
       'Hotligand', 'species', 'source', 'ki Note', 'ki Val', 'Reference',
       'Link'],
      dtype='object')
(98678, 14)


In [19]:
serotonin_df = df[df['Name'].str.contains('5-HT', case=False, na=False)]

#Remove rows with missing or invalid SMILES or Ki values 
serotonin_df = serotonin_df.dropna(subset=["SMILES", "ki Val"])
serotonin_df = serotonin_df[serotonin_df["ki Val"].apply(lambda x: str(x).replace(".", "", 1).isdigit())]
serotonin_df.shape

#Convert Ki values to numeric
serotonin_df["ki Val"] = serotonin_df["ki Val"].astype(float)
serotonin_df.head()

Name Unigene  Ligand ID          Ligand Name  \
Number                                                   
1       5-HT2C   HTR2C        172  5-Methoxytryptamine   
2       5-HT2C   HTR2C        172  5-Methoxytryptamine   
3       5-HT2C   HTR2C        172  5-Methoxytryptamine   
4       5-HT2C   HTR2C        172  5-Methoxytryptamine   
5       5-HT2C   HTR2C        172  5-Methoxytryptamine   

                          SMILES       CAS      NSC       Hotligand species  \
Number                                                                        
1       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
2       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
3       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
4       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   
5       COC1=CC2=C(C=C1)NC=C2CCN  608-07-1  56422.0  3H-MESULERGINE     PIG   

                source ki Note  ki Val                Reference Link  
Number                                                                
1       Choroid Plexus     NaN    23.4     HOYER, 1989 (J.R.R.)  NaN  
2       Choroid Plexus     NaN    23.4              HOYER, 1988  NaN  
3       Choroid Plexus     NaN    25.1  HOYER, 1988 or 9 (book)  NaN  
4       Choroid Plexus     NaN    43.7    MARKSTEIN ET AL, 1986  NaN  
5       Choroid Plexus     NaN    43.8        ENGEL ET AL, 1986  NaN

In [43]:
curated_df = serotonin_df[["Name", " Ligand Name", "SMILES", "ki Val", "Reference"]].rename(
    columns={"Name": "Receptor", "Ligand Name": "Ligand", "ki Val": "Ki_nM"}
)

curated_df.head()
curated_df.to_csv("curated_ki_database.csv", index=False)

Now that we have a curated dataset filtered with just the serotonin and removed the missing/invalid values, the next step is to generate molecular fingerprints (feature engineering) by turning each chemical structure (SMILES) into a numeric vector that machine learning models can understand. The output of the following steps generates a CSV where each row is a compound with 2048 features (presence/absence of chemical patterns) and a Ki value (binding affinity) --> this is the ML-ready dataset. 

In [35]:
standardizer = Standardizer()

def sanitize_and_fingerprint(smiles, radius=2, nBits=2048):
    try:
        mol = Chem.MolFromSmiles(str(smiles))
        if mol is None:
            return None
        mol = standardizer.standardize(mol)
        return AllChem.GetMorganFingerprintAsBitVect(mol, radius, nBits=nBits)
    except:
        return None

In [36]:
curated_df["Fingerprint"] = curated_df["SMILES"].apply(sanitize_and_fingerprint)
curated_df = curated_df[curated_df["Fingerprint"].notnull()]

[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerator
[14:26:44] DEPRECATION WARNING: please use MorganGenerat

In [37]:
fps = np.array([np.array(fp) for fp in curated_df["Fingerprint"]])
fps_df = pd.DataFrame(fps)
fps_df["Ki_nM"] = curated_df["Ki_nM"].values
fps_df.to_csv("fingerprints_with_ki.csv", index=False)


In [38]:
fps_df.head()

0  1  2  3  4  5  6  7  8  9  ...  2039  2040  2041  2042  2043  2044  \
0  0  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   
1  0  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   
2  0  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   
3  0  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   
4  0  0  0  0  0  0  0  0  0  0  ...     0     0     0     0     0     0   

   2045  2046  2047  Ki_nM  
0     0     0     0   23.4  
1     0     0     0   23.4  
2     0     0     0   25.1  
3     0     0     0   43.7  
4     0     0     0   43.8  

[5 rows x 2049 columns]

In [42]:
# 2. Split into features and target
X = fps_df.drop(columns=["Ki_nM"])
y = fps_df["Ki_nM"]

# 3. Train/test split
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42
)

# 4. Train model
model = RandomForestRegressor(n_estimators=100, random_state=42)
model.fit(X_train, y_train)

# 5. Evaluate model
y_pred = model.predict(X_test)
rmse = np.sqrt(mean_squared_error(y_test, y_pred))
r2 = r2_score(y_test, y_pred)

print(f"✅ R² Score: {r2:.3f}")
print(f"✅ RMSE: {rmse:.2f} nM")

# 6. Save model and predictions
joblib.dump(model, "rf_model.pkl")

pred_df = pd.DataFrame({
    "Actual_Ki_nM": y_test.values,
    "Predicted_Ki_nM": y_pred
})
pred_df.to_csv("test_predictions.csv", index=False)

✅ R² Score: 0.257
✅ RMSE: 4193.72 nM
